# Vertex AI Custom Training Job - Custom Training Job 구성 및 실행

이 노트북은 Vertex AI Custom Training Job을 이용한 모델 학습 과정을 단계별로 설명합니다.

In [ ]:
# 작업 1 - 기본 설정

import os
from google.cloud import aiplatform, storage
import subprocess

# 필요한 패키지 설치
subprocess.run(["pip", "install", "torch", "torchvision", "google-cloud-aiplatform", "google-cloud-storage", "pyyaml"])

import torch
import torchvision
import zipfile

# GCP 프로젝트 설정
PROJECT_ID = "prd-center-gcp"  # GCP 프로젝트 ID
REGION = "us-central1"  # 리전 설정
BUCKET_NAME = "test-coco-dataset-bucket"  # GCS 버킷 이름

# Vertex AI 초기화
aiplatform.init(project=PROJECT_ID, location=REGION)

In [ ]:
# 작업 2 - COCO 데이터셋 및 기계 학습 환경 다운로드

# COCO 데이터셋 및 학습 코드 다운로드
!wget https://github.com/ultralytics/assets/releases/download/v0.0.0/coco128.zip
!wget https://raw.githubusercontent.com/ultralytics/yolov5/master/data/coco128.yaml
!wget https://raw.githubusercontent.com/ultralytics/yolov5/master/train.py

# 데이터 압축 해제
import zipfile
with zipfile.ZipFile("coco128.zip", "r") as zip_ref:
    zip_ref.extractall("coco128")

In [ ]:
# 작업 3 - GCS 버킷 생성 및 업로드

# GCS 버킷 생성
storage_client = storage.Client()
bucket = storage_client.create_bucket(BUCKET_NAME, location=REGION)

# GCS 버킷에 업로드
!gsutil -m cp -r coco128 gs://{BUCKET_NAME}/coco/
!gsutil -m cp -r coco128.yaml gs://{BUCKET_NAME}/coco/
!gsutil -m cp -r train.py gs://{BUCKET_NAME}/coco/

In [ ]:
# 작업 4 - Dockerfile 및 entrypoint.sh 파일 생성

from pathlib import Path

# Dockerfile 내용
dockerfile_content = '''\
# 베이스 이미지: PyTorch GPU 기반
FROM gcr.io/deeplearning-platform-release/pytorch-gpu.1-12:latest

# 작업 디렉토리 생성
WORKDIR /app

# 필요한 패키지 설치
RUN apt-get update && \\
    apt-get install -y git gcc curl && \\
    pip install --upgrade pip

# YOLOv5 클론 및 의존성 설치
RUN git clone https://github.com/ultralytics/yolov5.git && \\
    cd yolov5 && \\
    pip install -r requirements.txt

# 진입점 스크립트 복사 (추후 작성)
COPY entrypoint.sh /app/entrypoint.sh
RUN chmod +x /app/entrypoint.sh

# 엔트리포인트 지정
ENTRYPOINT ["/app/entrypoint.sh"]
'''

# Entrypoint 스크립트 템플릿
entrypoint_content = '''\
#!/bin/bash
set -e

BUCKET_NAME="test-coco-dataset-bucket"

cd /app/yolov5

# 데이터 및 설정 다운로드 (사용자가 BUCKET_NAME을 수정해야 함)
gsutil -m cp -r gs://${BUCKET_NAME}/coco/coco128/coco128 .
gsutil -m cp gs://${BUCKET_NAME}/coco/coco128.yaml .
gsutil -m cp gs://${BUCKET_NAME}/coco/train.py .

# 학습 실행
python train.py --data=coco128.yaml --epochs=10 --batch-size=16 --img-size=640

# 결과 업로드
gsutil -m cp -r runs/train/* gs://${BUCKET_NAME}/coco/models/
'''

# 파일 생성
Path("Dockerfile").write_text(dockerfile_content)
Path("entrypoint.sh").write_text(entrypoint_content)

print("✅ Dockerfile 및 entrypoint.sh 파일이 생성되었습니다.")

In [ ]:
# 작업 5 - 학습용 컨테이너 이미지 생성

import subprocess

# 컨테이너 변수 설정
REPO_NAME="training-repo"
IMAGE_NAME = "yolo-train"
IMAGE_URI = f"{REGION}-docker.pkg.dev/{PROJECT_ID}/{REPO_NAME}/{IMAGE_NAME}:latest"

# Docker 빌드 실행 (현재 디렉토리에 Dockerfile, entrypoint.sh 존재해야 함)
subprocess.run(["docker", "build", "-t", IMAGE_URI, "."], check=True)

# 레포지토리 생성
!gcloud artifacts repositories create {REPO_NAME} \
  --repository-format=docker \
  --location={REGION} \

# Docker 인증
!gcloud auth configure-docker {REGION}-docker.pkg.dev

# Docker 이미지 푸시
subprocess.run(["docker", "push", IMAGE_URI], check=True)


In [ ]:
# 작업 6- Custom Training Job 실행

!gcloud ai custom-jobs create \
  --region=us-central1 \
  --display-name=yolo-training-job \
  --worker-pool-spec=machine-type=n1-standard-8,replica-count=1,accelerator-type=NVIDIA_TESLA_T4,accelerator-count=1,container-image-uri={IMAGE_URI}
